In [2]:
!pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 7.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 7.1 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [3]:
import torch
from transformers import BertTokenizer, BertForSequenceClassification, Trainer, TrainingArguments, EarlyStoppingCallback
from datasets import load_dataset, Dataset
from datasets import load_dataset_builder
from datasets import get_dataset_split_names


In [19]:
ds_builder = load_dataset_builder("wikimedia/structured-wikipedia", "20240916.en")

In [21]:
ds_builder.info.features

{'name': Value(dtype='string', id=None),
 'identifier': Value(dtype='int64', id=None),
 'abstract': Value(dtype='string', id=None),
 'version': {'identifier': Value(dtype='int64', id=None),
  'comment': Value(dtype='string', id=None),
  'tags': Sequence(feature=Value(dtype='string', id=None), length=-1, id=None),
  'is_minor_edit': Value(dtype='bool', id=None),
  'is_flagged_stable': Value(dtype='bool', id=None),
  'has_tag_needs_citation': Value(dtype='bool', id=None),
  'scores': {'damaging': {'prediction': Value(dtype='bool', id=None),
    'probability': {'false': Value(dtype='float64', id=None),
     'true': Value(dtype='float64', id=None)}},
   'goodfaith': {'prediction': Value(dtype='bool', id=None),
    'probability': {'false': Value(dtype='float64', id=None),
     'true': Value(dtype='float64', id=None)}},
   'revertrisk': {'prediction': Value(dtype='bool', id=None),
    'probability': {'false': Value(dtype='float64', id=None),
     'true': Value(dtype='float64', id=None)}}},
 

In [139]:
get_dataset_split_names("wikimedia/structured-wikipedia", "20240916.en")

['train']

In [6]:
datasets = load_dataset(
    "wikimedia/structured-wikipedia", "20240916.en", split="train", streaming=True)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/43.5k [00:00<?, ?B/s]

In [7]:
datasets

IterableDataset({
    features: ['name', 'identifier', 'abstract', 'version', 'event', 'url', 'date_created', 'date_modified', 'is_part_of', 'in_language', 'license', 'description', 'sections', 'infoboxes', 'main_entity', 'additional_entities', 'image'],
    num_shards: 1
})

In [81]:
# feature classes (need to iterate over more to get all, since empty features will return NoneType)
i = 0
for entry in datasets:
  for key in entry.keys():
    print(f"{key} is {type(entry[key])}")
  print("\n\n")
  i += 1
  if i == 1: break

name is <class 'str'>
identifier is <class 'int'>
abstract is <class 'NoneType'>
version is <class 'dict'>
event is <class 'dict'>
url is <class 'str'>
date_created is <class 'datetime.datetime'>
date_modified is <class 'datetime.datetime'>
is_part_of is <class 'dict'>
in_language is <class 'dict'>
license is <class 'list'>
description is <class 'str'>
sections is <class 'list'>
infoboxes is <class 'NoneType'>
main_entity is <class 'NoneType'>
additional_entities is <class 'NoneType'>
image is <class 'NoneType'>





In [ ]:
# Subsection types/names Examples (when looking at the links, the dataset seems to miss some subsections)
i = 0
for entry in datasets:
  print(entry['name'])
  print(entry['url'])
  print(type(entry['sections']))
  print(len(entry['sections']))
  for i in range(len(entry['sections'])):
    print(entry['sections'][i]['name'])
  print("===============")
  i += 1
  if i == 5: break

In [8]:
# Looking at examples of the sections feature, this is where the text is stored and also where the hyperlinks are stored.

i = 0
for entry in datasets:
  print(entry['sections'][0])
  i += 1
  if i == 10: break


{'type': 'section', 'name': 'Abstract', 'has_parts': None}
{'type': 'section', 'name': 'Abstract', 'has_parts': [{'type': 'list', 'value': None, 'has_parts': [{'type': 'list_item', 'value': 'REDIRECT List of Suits characters#Mike Ross', 'links': [{'url': 'https://en.wikipedia.org/wiki/List_of_Suits_characters#Mike_Ross', 'text': 'List of Suits characters#Mike Ross', 'images': None}], 'has_parts': None, 'name': None}], 'links': None, 'name': None}]}
{'type': 'section', 'name': 'Abstract', 'has_parts': [{'type': 'paragraph', 'value': 'REDIRECT # Second Polish Republic', 'has_parts': None, 'links': [{'url': 'https://en.wikipedia.org/wiki/Second_Polish_Republic', 'text': 'Second Polish Republic', 'images': None}], 'name': None}]}
{'type': 'section', 'name': 'Abstract', 'has_parts': [{'type': 'list', 'value': None, 'has_parts': [{'type': 'list_item', 'value': 'REDIRECT Writing system#Directionality', 'links': [{'url': 'https://en.wikipedia.org/wiki/Writing_system#Directionality', 'text': 'W

In [11]:
# Example of feature extraction.
# Trying to pull out number of links per entry, the urls of the links, the length of the text in characters, and the text itself.

dataset_urls = []
dataset_links = []
dataset_charlengths = []
dataset_texts = []

# we will look at i number of entried from the streaming dataset, the value for i is set at the end of the for loop
i = 0

for entry in datasets:
  # Only looks at first section, which is Abstract. Need to loop over full section list later
  # type(entry['sections']) is List
  links = 0
  urls =[]
  charlength = 0
  text = ""
  ### print(entry['name'])
  ### print(entry['url'])

  # check if 'sections' is empty or y
  if isinstance(entry['sections'], list):
    for key in entry['sections'][0].keys():
      subsection = entry['sections'][0][key]
      if key == 'has_parts' and isinstance(subsection, list):
        for sub_dict in subsection:
          for sub_key in sub_dict.keys():

            # Get text and character length from "value" if "type": "paragraph"
            if sub_dict[sub_key] == 'paragraph':
              charlength += len(sub_dict['value'])
              text += sub_dict['value']

            # Get link count and URLs from "links" if "links" contains a list (i.e. not NoneType)
            if sub_key == 'links':
              if isinstance(sub_dict[sub_key], list):
                links += len(sub_dict[sub_key])
                for link in sub_dict[sub_key]:
                  urls.append(link['url'])

            # If "has_parts" contains a list (i.e. not NoneType) then there is another layer that could contain more links
            if sub_key == 'has_parts' and isinstance(sub_dict[sub_key], list):
              subsubsection = sub_dict[sub_key]
              for subsub_dict in subsubsection:
                for subsub_key in subsub_dict.keys():
                  if subsub_key == 'links':
                    if isinstance(subsub_dict[subsub_key], list):
                      links += len(subsub_dict[subsub_key])
                      for link in subsub_dict[subsub_key]:
                        urls.append(link['url'])

                  # Check if there is another layer deeper, didn't find any after checking 10,000 entries
                  if subsub_key == 'has_parts' and isinstance(subsub_dict[subsub_key], list):
                    print("##there is even deeper to go")

  # append features to dataset-wide lists
  dataset_texts.append(text)
  dataset_charlengths.append(charlength)
  dataset_urls.append(urls)
  dataset_links.append(links)

  i += 1
  if i == 10000: break

print(dataset_links)
print(dataset_urls)
print(dataset_charlengths)
print(dataset_texts)

[0, 1, 1, 1, 1, 4, 7, 2, 5, 0, 1, 2, 4, 1, 8, 6, 6, 11, 1, 0, 5, 4, 7, 18, 4, 1, 3, 1, 6, 3, 0, 2, 8, 4, 7, 5, 0, 2, 5, 7, 5, 6, 4, 15, 1, 5, 20, 4, 5, 2, 3, 0, 7, 3, 0, 3, 3, 2, 5, 23, 4, 0, 16, 11, 6, 4, 2, 5, 1, 2, 0, 6, 9, 2, 2, 1, 1, 4, 2, 4, 1, 5, 0, 4, 2, 4, 34, 1, 7, 0, 1, 6, 11, 7, 2, 5, 7, 5, 5, 1, 8, 7, 1, 8, 5, 4, 2, 7, 6, 0, 4, 8, 25, 1, 5, 2, 4, 2, 5, 4, 2, 8, 2, 1, 7, 4, 1, 6, 2, 2, 5, 3, 3, 5, 1, 3, 2, 14, 10, 14, 1, 0, 1, 6, 2, 2, 5, 1, 9, 7, 9, 4, 1, 0, 6, 8, 9, 6, 11, 1, 18, 0, 3, 3, 5, 3, 3, 0, 9, 7, 0, 3, 3, 8, 5, 5, 3, 4, 5, 1, 1, 2, 0, 5, 4, 5, 3, 11, 2, 1, 3, 1, 3, 5, 1, 4, 7, 3, 7, 0, 11, 6, 1, 0, 3, 0, 5, 6, 7, 5, 1, 6, 3, 2, 5, 16, 5, 6, 5, 3, 8, 4, 9, 5, 5, 1, 7, 10, 5, 0, 1, 19, 1, 2, 5, 4, 10, 3, 9, 7, 5, 0, 9, 9, 11, 1, 4, 4, 7, 6, 6, 0, 1, 16, 1, 5, 2, 0, 3, 8, 2, 3, 6, 12, 18, 8, 14, 8, 5, 7, 4, 11, 7, 6, 8, 1, 3, 8, 10, 3, 4, 3, 10, 3, 2, 7, 4, 1, 4, 3, 6, 0, 2, 5, 4, 2, 0, 1, 6, 10, 13, 1, 0, 5, 1, 1, 9, 9, 4, 6, 2, 0, 3, 0, 6, 11, 4, 7, 3, 6, 1, 4, 0